In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
%cd /content/files

In [ ]:
!pip install -U bitsandbytes


In [ ]:
# Install required packages
!pip install torch transformers safetensors accelerate

import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
import json

class ChatBot:
    def __init__(self, model_path):
        # Initialize tokenizer and model
        self.tokenizer = AutoTokenizer.from_pretrained(model_path)
        self.model = AutoModelForCausalLM.from_pretrained(
            model_path,
            device_map="auto",
            torch_dtype=torch.float16
        )

    def chat(self, user_input, max_length=1000):
        # Prepare input
        inputs = self.tokenizer(user_input, return_tensors="pt").to(self.model.device)

        # Generate response
        with torch.no_grad():
            outputs = self.model.generate(
                **inputs,
                max_length=max_length,
                num_return_sequences=1,
                temperature=0.7,
                do_sample=True,
                pad_token_id=self.tokenizer.eos_token_id
            )

        # Decode and return response
        response = self.tokenizer.decode(outputs[0], skip_special_tokens=True)
        return response

# Simple chat interface
def start_chat():
    print("Initializing chatbot... This may take a few minutes.")
    chatbot = ChatBot("/content/files")  # Use the directory containing model files

    print("\nChat initialized! Type 'quit' to exit.")
    while True:
        user_input = input("\nYou: ")
        if user_input.lower() == 'quit':
            break

        response = chatbot.chat(user_input)
        print(f"\nBot: {response}")

# Start the chat
if __name__ == "__main__":
    start_chat()